# Building a Retrieval Augmented Generation (RAG) Chatbot

In [341]:
!pip install --quiet --upgrade langchain-text-splitters langchain-community langgraph
!pip install -qU langchain-mistralai
!pip install -qU langchain-chroma
# !pip install -qU chromadb
# !pip install xmltodict

# To correct UnstructuredXMLLoader errors
# !pip install "unstructured>=0.6.7"

## Setup

In [165]:
import getpass
import os

os.environ["LANGSMITH_TRACING"] = "true"
os.environ["LANGSMITH_API_KEY"] = getpass.getpass("Enter API key for Langsmith: ")

Enter API key for Langsmith:  ········


## Components

In [396]:
import getpass
import os

# Chat model

MODEL_NAME = "mistral-small-latest"
if "MISTRAL_API_KEY" not in os.environ:
    os.environ["MISTRAL_API_KEY"] = getpass.getpass("Enter API key for Mistral API: ")

Enter API key for Mistral AI:  ········


In [ ]:
from langchain_mistralai import ChatMistralAI, MistralAIEmbeddings

# Chat model initialization
llm = ChatMistralAI(
    mistral_api_key=MISTRAL_API_KEY,
    model="mistral-small-latest",
    streaming=True,
    temperature=0.6
)

# Embeddings model
embeddings = MistralAIEmbeddings(model="mistral-embed")

In [408]:
from langchain_chroma import Chroma

# Vector store
vector_store = Chroma(embedding_function=embeddings)

## Loading JSON and XML files

Transforming the data JSON and XML files we got online into LangChain Document objects

### Test: loading a single JSON file

In [11]:
import json
from pathlib import Path
from pprint import pprint

file_path="../parcoursup/parcoursup_data.json"
data = json.loads(Path(file_path).read_text())
pprint(data)

[{'acceptations': 0,
  'annee_du_bac': 2021,
  'doublette': 'Art,Art',
  'formation': 'Licence Chimie',
  'propositions_d_admissions': 0.0,
  'voeux': 0},
 {'acceptations': 0,
  'annee_du_bac': 2021,
  'doublette': 'Art,Art',
  'formation': 'Licence Langues et littÃ©ratures franÃ§aises',
  'propositions_d_admissions': 0.0,
  'voeux': 0},
 {'acceptations': 0,
  'annee_du_bac': 2021,
  'doublette': 'Art,Art',
  'formation': 'Licence Philosophie, EpistÃ©mologie',
  'propositions_d_admissions': 0.0,
  'voeux': 0},
 {'acceptations': 0,
  'annee_du_bac': 2021,
  'doublette': 'Art,Art',
  'formation': 'Licence Physique',
  'propositions_d_admissions': 0.0,
  'voeux': 0},
 {'acceptations': 0,
  'annee_du_bac': 2021,
  'doublette': 'Art,Art',
  'formation': 'Licence Pluri Droit - Sciences Ã©co - AES',
  'propositions_d_admissions': 0.0,
  'voeux': 0},
 {'acceptations': 0,
  'annee_du_bac': 2021,
  'doublette': 'Art,Art',
  'formation': 'Licence Pluri Langues',
  'propositions_d_admissions': 0.0

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [12]:
from langchain_community.document_loaders import JSONLoader

loader = JSONLoader(
    file_path="../parcoursup/parcoursup_data.json",
    jq_schema=".[]",
    text_content=False
)

documents = loader.load()
pprint(documents[0])

Document(metadata={'source': 'C:\\Users\\Laura GALINDO\\Documents\\Academique_et_pro\\Epitech Digital School\\Bootcamp Chatbot IA\\chatbot-orientation-pro\\parcoursup\\parcoursup_data.json', 'seq_num': 1}, page_content='{"annee_du_bac": 2021, "doublette": "Art,Art", "formation": "Licence Chimie", "voeux": 0, "propositions_d_admissions": 0, "acceptations": 0}')


### Test: loading a single XML file

In [14]:
from bs4 import BeautifulSoup

with open('../onisep/Onisep_Fiches_Formations.xml', 'r', encoding="utf-8") as f:
    data = f.read()

bs_data = BeautifulSoup(data, 'xml')

print(bs_data.prettify()[:500])

<?xml version="1.0" encoding="utf-8"?>
<formations xmlns:exsl="http://exslt.org/common">
 <formation>
  <identifiant>
   FOR.1000
  </identifiant>
  <code_scolarite>
   16X20003
  </code_scolarite>
  <libelle_complet>
   mastère spé. management de la qualité, de la sécurité et de l'environnement
  </libelle_complet>
  <sigle/>
  <libelle_generique/>
  <libelle_specifique/>
  <type_option/>
  <type_Formation>
   <type_formation_sigle>
    mastère spé.
   </type_formation_sigle>
   <type_formation


In [15]:
from langchain_community.document_loaders import UnstructuredXMLLoader
from pprint import pprint

loader = UnstructuredXMLLoader('../onisep/Onisep_Fiches_Formations.xml')

documents = loader.load()

print(documents[0].page_content[:500])

FOR.1000

16X20003

mastère spé. management de la qualité, de la sécurité et de l'environnement

mastère spé.

MASTERE SPE

mastère spécialisé

"1 an"

https://www.francecompetences.fr/recherche/rncp/37084/

200

Spécialités pluritechnologiques de la production

R

Contrôle, prévention, entretien

niveau 7

REF.423

bac + 6

16X

Label de la Conférence des grandes écoles (CGE)

Formation inscrite au RNCP

MET.878

chargé/e hygiène sécurité environnement (HSE)

chargée hygiène sécurité environnem


### Converting XML files to JSON files

The layout of Document objects loaded from XML files is too different from JSON files, and less well structured, so the MistralAI API cannot later embed them into the vector store

In [259]:
import json
import xmltodict

def convert_xml_to_json(xml_file: str, json_file: str):
    try:
        with open(xml_file, 'r', encoding='utf-8') as f:
            xml_content = f.read()

        data_dict = xmltodict.parse(xml_content)

        formations = data_dict.get("formations", {})
        if isinstance(formations, dict):
            formations = formations.get("formation", [])
        else:
            formations = []

        processed_formations = []

        for formation in formations:
            processed_entry = {}

            # Direct string fields
            processed_entry["identifiant"] = formation["identifiant"] if "identifiant" in formation else None
            processed_entry["libelle_complet"] = formation["libelle_complet"] if "libelle_complet" in formation else None
            processed_entry["duree_formation"] = formation["duree_formation"].strip('"') if "duree_formation" in formation else None
            processed_entry["url"] = formation["url"] if "url" in formation else None
            processed_entry["niveau_certification"] = formation["niveau_certification"] if "niveau_certification" in formation else None
            processed_entry["poursuites_etudes"] = formation["poursuites_etudes"] if "poursuites_etudes" in formation else None
            processed_entry["publications"] = formation["publications"] if "publications" in formation else None

            # Nested structures
            if "type_Formation" in formation and isinstance(formation["type_Formation"], dict):
                processed_entry["type_Formation"] = formation["type_Formation"].get("type_formation_libelle", None)
            else:
                processed_entry["type_Formation"] = None

            if "niveau_etudes" in formation and isinstance(formation["niveau_etudes"], dict):
                processed_entry["niveau_etudes"] = formation["niveau_etudes"].get("libelle", None)
            else:
                processed_entry["niveau_etudes"] = None

            if "nsf_discipline" in formation and isinstance(formation["nsf_discipline"], dict):
                processed_entry["nsf_discipline"] = formation["nsf_discipline"].get("NSF_discipline_libelle", None)
            else:
                processed_entry["nsf_discipline"] = None

            if "nature_certificat" in formation and isinstance(formation["nature_certificat"], dict):
                certif = formation["nature_certificat"].get("libelle_nature_certificat", None)
                processed_entry["nature_certificat"] = ", ".join(certif) if isinstance(certif, list) else certif
            else:
                processed_entry["nature_certificat"] = None

            # Handling "metiers_formation" properly
            processed_entry["metiers_formation"] = []
            if "metiers_formation" in formation and isinstance(formation["metiers_formation"], dict):
                metiers = formation["metiers_formation"].get("metier", [])

                if isinstance(metiers, dict):  # If there is only one "metier"
                    metiers = [metiers]

                for metier in metiers:
                    metier_data = {"nom_metier": metier.get("nom_metier", None), "synonymes": []}

                    if "synonymes" in metier and isinstance(metier["synonymes"], dict):
                        synonyms = metier["synonymes"].get("synonyme", [])

                        if isinstance(synonyms, dict):  # If there is only one synonym
                            synonyms = [synonyms]

                        metier_data["synonymes"] = [syn.get("nom_metier") for syn in synonyms if isinstance(syn, dict)]

                    processed_entry["metiers_formation"].append(metier_data)

            processed_formations.append(processed_entry)

        with open(json_file, 'w', encoding='utf-8') as f:
            json.dump(processed_formations, f, ensure_ascii=False, indent=4)

        print(f"Conversion réussie : '{xml_file}' → '{json_file}'")

    except Exception as e:
        print(f"Erreur lors de la conversion : {e}")

# Exemple d'utilisation
convert_xml_to_json("../onisep/Onisep_Fiches_Formations.xml", "../onisep/Onisep_Fiches_Formations.json")

Conversion réussie : '../onisep/Onisep_Fiches_Formations.xml' → '../onisep/Onisep_Fiches_Formations.json'


In [728]:
import json
import xmltodict

def convert_xml_to_json_2(xml_file: str, json_file: str):
    try:
        with open(xml_file, 'r', encoding='utf-8') as f:
            xml_content = f.read()

        data_dict = xmltodict.parse(xml_content)

        metiers = data_dict.get("metiers", {})
        if isinstance(metiers, dict):
            metiers = metiers.get("metier", [])
        else:
            metiers = []

        processed_metiers = []

        for metier in metiers:
            processed_entry = {}

            # Direct string fields
            processed_entry["identifiant"] = metier.get("identifiant")
            processed_entry["nom_metier"] = metier.get("nom_metier")
            processed_entry["libelle_feminin"] = metier.get("libelle_feminin")
            processed_entry["libelle_masculin"] = metier.get("libelle_masculin")
            processed_entry["competences"] = metier.get("competences")
            processed_entry["condition_travail"] = metier.get("condition_travail")
            processed_entry["nature_travail"] = metier.get("nature_travail")
            processed_entry["acces_metier"] = metier.get("acces_metier")
            processed_entry["vie_professionnelle"] = metier.get("vie_professionnelle")
            processed_entry["accroche_metier"] = metier.get("accroche_metier")

            # Nested structures
            if "romesV3" in metier and isinstance(metier["romesV3"], dict):
                processed_entry["romesV3"] = metier["romesV3"].get("romesV3")
            else:
                processed_entry["romesV3"] = None

            if "niveau_acces_min" in metier and isinstance(metier["niveau_acces_min"], dict):
                processed_entry["niveau_acces_min"] = metier["niveau_acces_min"].get("libelle")
            else:
                processed_entry["niveau_acces_min"] = None

            # Deep-nested structures

            # Traitement des synonymes
            processed_entry["synonymes"] = []
            if "synonymes" in metier and isinstance(metier["synonymes"], dict):
                synonymes = metier["synonymes"].get("synonyme", [])
                if isinstance(synonymes, dict):  # Si il n'y a qu'un "synonyme"
                    synonymes = [synonymes]
                for synonyme in synonymes:
                    synonyme_data = {"nom_metier": synonyme.get("nom_metier")}
                    processed_entry["synonymes"].append(synonyme_data)

            # Traitement des statuts
            processed_entry["statuts"] = []
            if "statuts" in metier and isinstance(metier["statuts"], dict):
                statuts = metier["statuts"].get("statut", [])
                if isinstance(statuts, dict):  # Si il n'y a qu'un "statut"
                    statuts = [statuts]
                for statut in statuts:
                    statut_data = {"libelle": statut.get("libelle")}
                    processed_entry["statuts"].append(statut_data)

            # Traitement des metiers_associes
            processed_entry["metiers_associes"] = []
            if "metiers_associes" in metier and isinstance(metier["metiers_associes"], dict):
                metiers_associes = metier["metiers_associes"].get("metier_associe", [])
                if isinstance(metiers_associes, dict):  # Si il n'y a qu'un "metier_associe"
                    metiers_associes = [metiers_associes]
                for metier_associe in metiers_associes:
                    metier_associe_data = {"libelle": metier_associe.get("libelle")}
                    processed_entry["metiers_associes"].append(metier_associe_data)

            # Traitement des formations_min_requise
            processed_entry["formations_min_requise"] = []
            if "formations_min_requise" in metier and isinstance(metier["formations_min_requise"], dict):
                formations_min_requise = metier["formations_min_requise"].get("formation_min_requise", [])
                if isinstance(formations_min_requise, dict):  # Si il n'y a qu'une "formation_min_requise"
                    formations_min_requise = [formations_min_requise]
                for formation in formations_min_requise:
                    formation_data = {"libelle": formation.get("libelle")}
                    processed_entry["formations_min_requise"].append(formation_data)

            # Traitement des secteurs_activite
            processed_entry["secteurs_activite"] = []
            if "secteurs_activite" in metier and isinstance(metier["secteurs_activite"], dict):
                secteurs_activite = metier["secteurs_activite"].get("secteur_activite", [])
                if isinstance(secteurs_activite, dict):  # Si il n'y a qu'un "secteur_activite"
                    secteurs_activite = [secteurs_activite]
                for secteur in secteurs_activite:
                    secteur_data = {"libelle": secteur.get("libelle")}
                    processed_entry["secteurs_activite"].append(secteur_data)

            # Traitement des centres_interet
            processed_entry["centres_interet"] = []
            if "centres_interet" in metier and isinstance(metier["centres_interet"], dict):
                centres_interet = metier["centres_interet"].get("centre_interet", [])
                if isinstance(centres_interet, dict):  # Si il n'y a qu'un "centre_interet"
                    centres_interet = [centres_interet]
                for centre in centres_interet:
                    centre_data = {"libelle": centre.get("libelle")}
                    processed_entry["centres_interet"].append(centre_data)

            processed_metiers.append(processed_entry)

        with open(json_file, 'w', encoding='utf-8') as f:
            json.dump(processed_metiers, f, ensure_ascii=False, indent=4)

        print(f"Conversion réussie : '{xml_file}' → '{json_file}'")

    except Exception as e:
        print(f"Erreur lors de la conversion : {e}")

# Exemple d'utilisation
convert_xml_to_json_2("../onisep/Onisep_Fiches_Metiers.xml", "../onisep/Onisep_Fiches_Metiers.json")

Conversion réussie : '../onisep/Onisep_Fiches_Metiers.xml' → '../onisep/Onisep_Fiches_Metiers.json'


### Loading multiple JSON files as LangChain Document objects

In [730]:
import os
import json
from pathlib import Path
from langchain.docstore.document import Document
from langchain_community.document_loaders import JSONLoader, UnstructuredXMLLoader

# To correct UnstructuredXMLLoader errors
# import nltk
# nltk.download('punkt')
# nltk.download('averaged_perceptron_tagger')

def load_json_documents(file_path: str) -> list:
    """
    Load a JSON file using JSONLoader and return a list of Documents
    """
    loader = JSONLoader(
        file_path=file_path,
        jq_schema=".[]",
        text_content=False,
    )
    try:
        documents = loader.load()
        print(f"[JSON] Loaded file: {file_path} ({len(documents)} document(s))")
        return documents
    except Exception as e:
        print(f"Error while loading JSON file {file_path} : {e}")
        return []

# def load_xml_documents(file_path: str) -> list:
#    """
#    Load an XML file using UnstructuredXMLLoader and return a list of Documents
#    """
#    loader = UnstructuredXMLLoader(file_path)
#    try:
#        documents = loader.load()
#        print(f"[XML] Loaded file: {file_path} ({len(documents)} document(s))")
#        return documents
#    except Exception as e:
#        print(f"Error while loading XML file {file_path} : {e}")
#        return []

def load_documents(file_paths: list) -> list:
    """
    For each file in the list, we determine its extension and call the appropriate loader
    (JSONLoader or UnstructuredXMLLoader), and then return a complete list of Documents
    """
    documents = []
    for fp in file_paths:
        ext = Path(fp).suffix.lower()
        if ext == ".json":
            documents.extend(load_json_documents(fp))
#        elif ext == ".xml":
#            documents.extend(load_xml_documents(fp))
        else:
            print(f"Unsupported file (extension {ext}) : {fp}")
    return documents

def export_documents(documents: list):
    """
    Save the Document objects to a text file for inspection or debugging
    """
    with open("loaded_documents.txt", "w", encoding="utf-8") as f:
        for doc in documents:
            f.write(f"Source: {doc.metadata.get('source')}\n")
            f.write(f"Content:\n{doc.page_content}\n\n---\n\n")
    
    print("Documents saved to 'loaded_documents.txt'")

In [ ]:
# List of JSON and XML files to load
file_list = [
    # DONE:
    # "../parcoursup/parcoursup_data.json",
    # "../mon_master/monmaster_data.json",
    # "../salons/salons_january.json",
    # "../salons/salons_february.json",
    # "../salons/salons_march.json",
    # "../salons/salons_may_june.json"
    # "../France_travail/Competences-themes.json",
    # "../France_travail/Francetravail Scraper debutant.json",
    # "../France_travail/Francetravail Scraper junior .json",
    # "../France_travail/Francetravail_Scraper_Global.json",
    # "../France_travail/Nombre_offres_themes.json",
    # "../mbti/mbti_jobs.json",
    # "../onisep/Onisep_Fiches_Formations.json",
    #"../onisep/Onisep_Fiches_Metiers.json",
    
]

# Load all the documents
all_documents = load_documents(file_list)

print(f"\nTotal number of loaded documents: {len(all_documents)}")

export_documents(all_documents)

In [ ]:
from langchain_text_splitters import RecursiveCharacterTextSplitter

def dynamic_split_documents(documents, base_chunk_size=1000, min_chunks=3, max_chunks=200):
    """
    Dynamically split a list of documents into smaller chunks based on document size
    
    Parameters:
        - documents: List of LangChain Document objects
        - base_chunk_size: Default chunk size in characters
        - min_chunks: Minimum number of chunks per document
        - max_chunks: Maximum number of chunks per document
    
    Returns:
        - List of split documents
    """
    all_splits = []
    
    for doc in documents:
        doc_length = len(doc.page_content)
        
        # Dynamically adjust the chunk size:
        # - Ensure chunks are not too small by using at least `base_chunk_size`
        # - Ensure chunks are not too big by keeping at least `min_chunks` per document
        # - This balances the number and size of chunks for better retrieval
        chunk_size = max(base_chunk_size, doc_length // max_chunks)  # Prevents chunks from being too tiny
        chunk_size = min(chunk_size, doc_length // min_chunks)  # Ensures we don't have too few large chunks
        
        # Define the text splitter
        text_splitter = RecursiveCharacterTextSplitter(
            chunk_size=chunk_size,
            chunk_overlap=chunk_size // 5,  # 20% overlap
            add_start_index=True # Keeps track of where in the original document each chunk came from
        )
        
        # Split the document and extend the list
        splits = text_splitter.split_documents([doc])
        # print(f"Document: {doc.metadata.get('source')} | Original Length: {len(doc.page_content)} | Chunks Created: {len(splits)}")
        
        all_splits.extend(splits) # Adds all the elements in splits to all_splits, one by one
    
    print(f"\nTotal number of chunks created: {len(all_splits)}")
    return all_splits

def export_split_documents(chunks):
    """
    Save the split documents to a text file with delimiters between chunks

    Each document chunk's source and content are written to 'split_documents.txt', 
    with '---' as a separator between different chunks.

    Parameters:
        - chunks (list): A list of LangChain Document objects after splitting

    Returns:
        - File containing all split document chunks with delimiters
    """
    with open("split_documents.txt", "w", encoding="utf-8") as f:
        for i, chunk in enumerate(chunks):
            # Add delimiter before every chunk except the first one
            if i > 0:
                f.write("\n---\n\n")

            f.write(f"Source: {chunk.metadata.get('source')}\n")
            f.write(f"Content:\n{chunk.page_content}\n")

    print("Split documents saved to 'split_documents.txt'")


# Split the loaded documents
split_documents = dynamic_split_documents(all_documents)

export_split_documents(split_documents)

## Storing Document splits

Indexing our chunks of documents to be able to vector search over them at runtime, which entails embedding the contents of each chunk of Document into the Chroma vector store

In [ ]:
import time

def batch_embed_documents(split_documents, vector_store, batch_size=10, sleep_time=2):
    """
    Embed Documents in batches and add them to the vector store

    Parameters:
        - split_documents (list): List of document chunks to embed
        - vector_store: The vector database where embeddings are stored
        - batch_size (int): Number of documents per batch (default is 10)
        - sleep_time (int): Time to wait (in seconds) between batches to avoid API rate limits (default is 2)
    
    Returns:
        - None
    """
    for i in range(0, len(split_documents), batch_size):
        batch = [chunk for chunk in split_documents[i:i + batch_size]]

        try:
            document_ids = vector_store.add_documents(documents=batch)
            print(f"Batch {i // batch_size + 1}: {document_ids[:3]}")
        except Exception as e:
            print(f"Error in batch {i // batch_size + 1}: {e}")

        time.sleep(sleep_time)  # Pause to prevent API rate limiting


batch_embed_documents(split_documents, vector_store)

In [745]:
# Number of Document objects stored in our vector store
print("Number of Documents:")
print(vector_store._collection.count())

# IDs of the first 10 Documents stored in our vector store
print("\nIDs of the first 10 Documents stored in the vector store:")
print(vector_store._collection.get()["ids"][:10])

# Test query on our vector store
query = "gouvernement"
print(f'\nQuerying "{query}" on our vector store:')
results = vector_store.similarity_search(query, k=3)
for doc in results:
    print(doc.page_content)

Number of Documents:
160472

IDs of the first 10 Documents stored in the vector store:
['e4e290e7-3ad0-4d26-8c13-078ae83824f4', '719fe31e-7cbd-4152-9cf2-5262553ffa01', '0493492c-a637-4bcb-a4f7-2f597daca379', 'e4ea8808-f8f7-4690-9304-bf222d227ee7', '5e5ee20a-1dac-4b75-aa25-86c65dcf4257', 'ff2bfd8a-083f-4d48-a908-829cac595dd7', '818fcd79-c451-4f65-bfa0-8d1068b32c0b', 'eb59f67c-0fdd-4435-b1da-7251d52c1983', '6a2ebf7c-ca2c-4706-b176-1c8514bd7059', 'd7669c3a-e27e-4c6d-8cac-ad2e666db1e9']

Querying "gouvernement" on our vector store:
G\u00e9opolitique et Sciences politiques", "formation": "Formations
G\u00e9opolitique et Sciences politiques", "formation": "Formations
G\u00e9opolitique et Sciences politiques", "formation": "Formations


## Embedding the documents and persisting the vector store to a ChromaDB (vectorial) database

In [907]:
import time
import chromadb
from chromadb import PersistentClient

# Define database path & collection name
DB_PATH = "./final_chroma_db"  
COLLECTION_NAME = "final_vector_store_collection"  
BATCH_SIZE = 50
DELAY = 5

# 1️⃣ Connect to ChromaDB and create a new collection
client = PersistentClient(path=DB_PATH)
try:
    client.delete_collection(name=COLLECTION_NAME)
    print(f"🗑️ Old collection '{COLLECTION_NAME}' deleted.")
except Exception:
    pass  # If it doesn't exist, no issue
collection = client.get_or_create_collection(name=COLLECTION_NAME)
print(f"✅ New collection '{COLLECTION_NAME}' created in '{DB_PATH}'.")

# 2️⃣ Load documents from the vector store
stored_data = vector_store.get()

if "documents" not in stored_data or not stored_data["documents"]:
    raise ValueError("❌ ERROR: No documents found in the vector store!")

documents = stored_data["documents"]
num_documents = len(documents)
print(f"📂 {num_documents} documents found in the vector store.")

# 3️⃣ Generate embeddings in batches
print("🔄 Generating embeddings for documents in batches...")
generated_embeddings = []

for i in range(0, num_documents, BATCH_SIZE):
    batch_docs = documents[i:i + BATCH_SIZE]
    try:
        batch_embeddings = embeddings.embed_documents(batch_docs)
        generated_embeddings.extend(batch_embeddings)
        print(f"✅ Processed batch {i // BATCH_SIZE + 1}/{num_documents // BATCH_SIZE + 1}")
    except Exception as e:
        print(f"❌ Error processing (generating embedding) batch {i // BATCH_SIZE + 1}: {e}")
    time.sleep(DELAY)  # Increased delay to avoid rate limiting

# Double-check length consistency
num_embeddings = len(generated_embeddings)
if len(stored_data["ids"]) != num_documents or num_embeddings != num_documents:
    print("❌ ERROR: Mismatch in lengths! Ensure 'ids', 'embeddings', and 'documents' have the same size.")

print(f"✅ Generated {num_embeddings} embeddings.")

# 4️⃣ Insert all embeddings & documents into ChromaDB
print("📥 Storing documents & embeddings in ChromaDB...")

for i in range(0, num_documents, BATCH_SIZE):
    batch_ids = stored_data["ids"][i:i + BATCH_SIZE]
    batch_embeddings = generated_embeddings[i:i + BATCH_SIZE]
    batch_documents = documents[i:i + BATCH_SIZE]
    batch_metadatas = stored_data.get("metadatas", [None] * num_documents)[i:i + BATCH_SIZE]

    # Check if metadatas are provided and have the correct length
    if batch_metadatas == [None] * len(batch_documents):
        print("⚠️ Warning: No metadata provided for this batch.")
    elif len(batch_metadatas) != len(batch_documents):
        print("❌ ERROR: Mismatch in lengths between metadatas and documents!")

    try:
        collection.add(
            ids=batch_ids,
            embeddings=batch_embeddings,
            documents=batch_documents,
            metadatas=batch_metadatas
        )
    except Exception as e:
        print(f"❌ Error processing (inserting embedding) batch {i // BATCH_SIZE + 1}: {e}")

    time.sleep(DELAY)  # Add delay between batches

print(f"🎉 Successfully stored {num_documents} documents & embeddings in '{DB_PATH}/{COLLECTION_NAME}'!")

🗑️ Old collection 'final_vector_store_collection' deleted.
✅ New collection 'final_vector_store_collection' created in './final_chroma_db'.
📂 160472 documents found in the vector store.
🔄 Generating embeddings for documents in batches...
✅ Processed batch 1/3210
✅ Processed batch 2/3210
✅ Processed batch 3/3210
✅ Processed batch 4/3210
✅ Processed batch 5/3210
✅ Processed batch 6/3210
✅ Processed batch 7/3210
✅ Processed batch 8/3210
✅ Processed batch 9/3210
✅ Processed batch 10/3210
✅ Processed batch 11/3210
✅ Processed batch 12/3210
✅ Processed batch 13/3210
✅ Processed batch 14/3210
✅ Processed batch 15/3210
✅ Processed batch 16/3210
✅ Processed batch 17/3210
✅ Processed batch 18/3210
✅ Processed batch 19/3210
✅ Processed batch 20/3210
✅ Processed batch 21/3210
✅ Processed batch 22/3210
✅ Processed batch 23/3210
✅ Processed batch 24/3210
✅ Processed batch 25/3210
✅ Processed batch 26/3210
✅ Processed batch 27/3210
✅ Processed batch 28/3210
✅ Processed batch 29/3210
✅ Processed batch

An error occurred with MistralAI: Client error '429 Too Many Requests' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/429


❌ Error processing (generating embedding) batch 1019: Client error '429 Too Many Requests' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/429


An error occurred with MistralAI: Client error '429 Too Many Requests' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/429


❌ Error processing (generating embedding) batch 1020: Client error '429 Too Many Requests' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/429
✅ Processed batch 1021/3210
✅ Processed batch 1022/3210


...

❌ Error processing (generating embedding) batch 3207: Client error '429 Too Many Requests' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/429


An error occurred with MistralAI: Client error '429 Too Many Requests' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/429


❌ Error processing (generating embedding) batch 3208: Client error '429 Too Many Requests' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/429


An error occurred with MistralAI: Client error '429 Too Many Requests' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/429


❌ Error processing (generating embedding) batch 3209: Client error '429 Too Many Requests' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/429
✅ Processed batch 3210/3210
❌ ERROR: Mismatch in lengths! Ensure 'ids', 'embeddings', and 'documents' have the same size.
✅ Generated 104772 embeddings.
📥 Storing documents & embeddings in ChromaDB...
❌ Error processing (inserting embedding) batch 2096: Unequal lengths for fields: ids: 50, metadatas: 50, embeddings: 22, documents: 50 in add.
❌ Error processing (inserting embedding) batch 2097: Expected Embedings to be non-empty list or numpy array, got [] in add.
❌ Error processing (inserting embedding) batch 2098: Expected Embedings to be non-empty list or numpy array, got [] in add.
❌ Error processing (inserting embedding) batch 2099: Expected Embedings to be non-empty list or numpy array, got [] in add.
❌ Error processing (inserting embedding) batch 2100: Expe

In [939]:
import time

num_stored = len(generated_embeddings)

if num_stored < num_documents:
    print(f"⚠️ {num_documents - num_stored} documents manquent des embeddings. Relançons le traitement...")

    missing_docs = [
        1019, 1020, 1023, 1024, 1027, 1028, 1029, 1037, 1040, 1045, 1046, 1049, 1052, 1053, 1054, 1060, 1064, 1065, 1066, 1067,
        1073, 1074, 1075, 1076, 1077, 1080, 1083, 1087, 1090, 1092, 1097, 1099, 1102, 1103, 1105, 1106, 1107, 1110, 1112, 1114,
        1116, 1119, 1123, 1124, 1127, 1128, 1129, 1132, 1133, 1134, 1136, 1138, 1139, 1141, 1142, 1144, 1146, 1149, 1152, 1153,
        1157, 1158, 1159, 1160, 1164, 1167, 1168, 1169, 1170, 1171, 1172, 1173, 1177, 1178, 1179, 1182, 1186, 1188, 1189, 1190,
        1191, 1193, 1196, 1200, 1203, 1207, 1209, 1213, 1217, 1219, 1221, 1224, 1233, 1234, 1235, 1236, 1240, 1241, 1242, 1246,
        1249, 1254, 1255, 1256, 1257, 1258, 1259, 1262, 1270, 1272, 1274, 1275, 1276, 1278, 1281, 1291, 1293, 1294, 1295, 1298,
        1299, 1302, 1303, 1304, 1305, 1306, 1308, 1318, 1320, 1321, 1322, 1323, 1325, 1326, 1328, 1330, 1331, 1332, 1336, 1339,
        1341, 1342, 1343, 1346, 1355, 1357, 1358, 1361, 1362, 1363, 1364, 1365, 1366, 1367, 1369, 1370, 1372, 1373, 1376, 1377,
        1378, 1379, 1380, 1382, 1383, 1385, 1388, 1389, 1394, 1396, 1397, 1398, 1400, 1404, 1405, 1406, 1408, 1411, 1412, 1417,
        1418, 1424, 1427, 1431, 1432, 1437, 1442, 1444, 1448, 1450, 1451, 1452, 1461, 1462, 1464, 1465, 1469, 1470, 1474, 1476,
        1477, 1481, 1482, 1483, 1488, 1489, 1493, 1497, 1500, 1502, 1504, 1508, 1509, 1510, 1512, 1513, 1514, 1515, 1518, 1520,
        1521, 1523, 1524, 1525, 1531, 1533, 1534, 1536, 1539, 1542, 1550, 1551, 1554, 1556, 1558, 1561, 1563, 1564, 1568, 1569,
        1570, 1571, 1572, 1574, 1576, 1579, 1582, 1584, 1592, 1595, 1596, 1598, 1600, 1601, 1604, 1608, 1609, 1611, 1612, 1613,
        1614, 1615, 1616, 1618, 1619, 1621, 1625, 1631, 1636, 1637, 1638, 1640, 1641, 1642, 1643, 1644, 1648, 1653, 1654, 1656,
        1658, 1664, 1672, 1675, 1676, 1677, 1679, 1682, 1685, 1686, 1690, 1695, 1696, 1698, 1699, 1701, 1704, 1708, 1709, 1710,
        1713, 1716, 1717, 1718, 1720, 1722, 1723, 1725, 1726, 1727, 1728, 1735, 1736, 1737, 1738, 1742, 1744, 1747, 1750, 1752,
        1755, 1757, 1758, 1759, 1763, 1766, 1767, 1768, 1770, 1771, 1772, 1779, 1781, 1782, 1783, 1784, 1785, 1786, 1791, 1793,
        1794, 1795, 1796, 1797, 1801, 1803, 1806, 1808, 1813, 1814, 1816, 1817, 1820, 1824, 1825, 1826, 1827, 1830, 1831, 1833,
        1834, 1837, 1838, 1840, 1841, 1842, 1849, 1850, 1852, 1853, 1857, 1864, 1865, 1878, 1879, 1881, 1882, 1884, 1885, 1894,
        1896, 1897, 1898, 1901, 1904, 1906, 1907, 1908, 1910, 1911, 1913, 1914, 1915, 1917, 1922, 1923, 1928, 1929, 1931, 1932,
        1933, 1934, 1935, 1941, 1942, 1943, 1949, 1954, 1955, 1956, 1957, 1958, 1959, 1965, 1969, 1970, 1971, 1972, 1973, 1974,
        1976, 1977, 1983, 1984, 1985, 1986, 1989, 1990, 1992, 1998, 1999, 2000, 2001, 2003, 2004, 2005, 2009, 2010, 2011, 2012,
        2014, 2015, 2017, 2020, 2022, 2023, 2025, 2027, 2032, 2033, 2035, 2036, 2037, 2039, 2042, 2043, 2045, 2047, 2050, 2052,
        2055, 2057, 2059, 2060, 2061, 2062, 2063, 2066, 2067, 2068, 2071, 2077, 2078, 2083, 2086, 2087, 2088, 2089, 2091, 2094,
        2549, 2550, 2552, 2554, 2557, 2563, 2567, 2573, 2574, 2575, 2590, 2591, 2592, 2593, 2594, 2595, 2597, 2599, 2600, 2601,
        2602, 2603, 2607, 2612, 2614, 2615, 2616, 2617, 2619, 2626, 2630, 2631, 2636, 2637, 2638, 2640, 2641, 2642, 2643, 2644,
        2645, 2646, 2649, 2651, 2652, 2653, 2654, 2655, 2656, 2658, 2659, 2662, 2664, 2665, 2666, 2667, 2668, 2669, 2670, 2671,
        2672, 2673, 2674, 2675, 2677, 2678, 2682, 2683, 2686, 2692, 2693, 2694, 2695, 2696, 2697, 2698, 2699, 2700, 2704, 2705,
        2707, 2709, 2710, 2711, 2712, 2713, 2714, 2715, 2716, 2718, 2723, 2728, 2731, 2736, 2737, 2739, 2741, 2744, 2745, 2746,
        2747, 2748, 2749, 2750, 2752, 2753, 2754, 2756, 2757, 2758, 2762, 2763, 2764, 2765, 2768, 2769, 2770, 2771, 2772, 2773,
        2774, 2775, 2776, 2779, 2780, 2781, 2782, 2783, 2784, 2785, 2787, 2790, 2791, 2793, 2795, 2796, 2798, 2799, 2800, 2801,
        2802, 2803, 2806, 2807, 2808, 2809, 2810, 2812, 2813, 2814, 2815, 2817, 2818, 2819, 2821, 2822, 2823, 2824, 2825, 2828,
        2835, 2847, 2848, 2849, 2851, 2852, 2853, 2858, 2861, 2862, 2866, 2870, 2872, 2874, 2880, 2881, 2882, 2883, 2885, 2888,
        2890, 2891, 2899, 2901, 2902, 2909, 2918, 2919, 2922, 2923, 2924, 2926, 2929, 2930, 2937, 2945, 2947, 2951, 2952, 2955,
        2965, 2966, 2967, 2968, 2969, 2970, 2972, 2974, 2978, 2979, 2980, 2981, 2982, 2983, 2985, 2986, 2992, 2993, 2994, 2995,
        2997, 2998, 2999, 3000, 3003, 3004, 3010, 3012, 3013, 3014, 3015, 3016, 3017, 3018, 3019, 3020, 3021, 3022, 3023, 3025,
        3026, 3027, 3028, 3029, 3030, 3031, 3032, 3033, 3034, 3035, 3036, 3038, 3039, 3040, 3041, 3042, 3043, 3044, 3045, 3046,
        3048, 3049, 3050, 3051, 3052, 3053, 3054, 3055, 3057, 3058, 3060, 3061, 3062, 3063, 3064, 3065, 3066, 3067, 3068, 3070,
        3071, 3072, 3073, 3074, 3075, 3076, 3077, 3079, 3080, 3081, 3083, 3084, 3085, 3086, 3087, 3088, 3089, 3090, 3091, 3092,
        3093, 3094, 3095, 3096, 3097, 3098, 3099, 3100, 3101, 3102, 3103, 3104, 3105, 3106, 3107, 3108, 3109, 3110, 3111, 3112,
        3113, 3114, 3115, 3116, 3117, 3118, 3119, 3120, 3121, 3122, 3123, 3124, 3125, 3126, 3127, 3128, 3129, 3130, 3131, 3132,
        3133, 3134, 3135, 3136, 3137, 3138, 3139, 3140, 3141, 3142, 3143, 3144, 3145, 3146, 3147, 3148, 3149, 3150, 3151, 3152,
        3153, 3154, 3155, 3156, 3157, 3158, 3159, 3160, 3161, 3162, 3163, 3164, 3165, 3166, 3167, 3168, 3169, 3170, 3171, 3172,
        3173, 3174, 3175, 3176, 3177, 3178, 3179, 3180, 3181, 3182, 3183, 3184, 3185, 3186, 3187, 3188, 3189, 3190, 3191, 3192,
        3193, 3194, 3195, 3196, 3197, 3198, 3199, 3200, 3201, 3202, 3203, 3204, 3205, 3206, 3207, 3208, 3209
    ]

    BATCH_SIZE = 50

    retry_embeddings = []
    retry_ids = []

    for i in range(0, len(missing_docs), BATCH_SIZE):
        batch_ids = missing_docs[i:i + BATCH_SIZE]

        # Convertir les IDs en textes
        batch_docs = [stored_data["documents"].get(str(doc_id), "") for doc_id in batch_ids]

        while True:
            try:
                batch_embeddings = embeddings.embed_documents(batch_docs)
                retry_embeddings.extend(batch_embeddings)
                retry_ids.extend(batch_ids)
                print(f"✅ Processed batch {missing_docs[i]}")
                break
            except Exception as e:
                if "429" in str(e):
                    print("🚨 429 Too Many Requests! 60 seconds break before retrying...")
                    time.sleep(60)
                else:
                    print(f"❌ Erreur : {e}")
                    raise

    # 🏗️ Ajouter les embeddings manquants dans ChromaDB
    print("📥 Insertion des embeddings manquants dans ChromaDB...")
    for i in range(0, len(retry_embeddings), BATCH_SIZE):
        collection.add(
            ids=[str(doc_id) for doc_id in retry_ids[i:i + BATCH_SIZE]],
            embeddings=retry_embeddings[i:i + BATCH_SIZE],
            documents=[stored_data["documents"].get(str(doc_id), "") for doc_id in retry_ids[i:i + BATCH_SIZE]],
            metadatas=[stored_data.get("metadatas", [{}])[int(doc_id)] for doc_id in retry_ids[i:i + BATCH_SIZE]]
        )
        print(f"✅ Inserted batch {i+1} into database")

    print(f"✅ {len(retry_embeddings)} embeddings manquants ajoutés avec succès !")

else:
    print("✅ Aucun document manquant. Tout est bien inséré !")

⚠️ 55700 documents manquent des embeddings. Relançons le traitement...


AttributeError: 'list' object has no attribute 'get'

In [929]:
# Retrieve stored embeddings from ChromaDB
stored_ids = collection.get()["ids"]

# Retrieve stored IDs from ChromaDB
stored_ids = collection.get()["ids"]

# Check if all IDs are unique
if len(stored_ids) == len(set(stored_ids)):
    print(f"✅ All {len(stored_ids)} embeddings in ChromaDB have distinct IDs.")
else:
    print(f"⚠️ Duplicate IDs detected in ChromaDB! Unique IDs: {len(set(stored_ids))}, Total IDs: {len(stored_ids)}")

# Compare with the original vector store
if len(stored_ids) == num_embeddings:
    print(f"✅ All {num_embeddings} embeddings were successfully stored in ChromaDB!")
else:
    print(f"⚠️ Mismatch detected! {len(stored_ids)} embeddings found in ChromaDB, expected {num_embeddings}.")

✅ All 104750 embeddings in ChromaDB have distinct IDs.
⚠️ Mismatch detected! 104750 embeddings found in ChromaDB, expected 104772.


In [431]:
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain.chains import create_retrieval_chain
from langchain import hub

def build_retrieval_chain(vector_store, llm, k=5):
    """
    Build a retrieval chain using a given vector store and LLM
    
    Parameters:
        - vector_store: The vector store containing document embeddings
        - llm: The language model to generate responses
        - k: Number of most relevant document chunks to retrieve (default is 5)
    
    Returns:
        - retrieval_chain: A LangChain retrieval chain object.
    """
    # Create a retriever from the vector store
    retriever = vector_store.as_retriever(search_kwargs={"k": k})
    
    # Load a pre-defined prompt template for retrieval-based Q&A
    retrieval_chat_prompt = hub.pull("langchain-ai/retrieval-qa-chat")
    
    # Create a document combination chain
    combine_docs_chain = create_stuff_documents_chain(llm, retrieval_chat_prompt)
    
    # Create and return the retrieval chain
    return create_retrieval_chain(retriever, combine_docs_chain)

## LLM Prompt-Engineering

In this part, we implement an advanced AI chatbot using LangChain and LangGraph.
It integrates :
- RAG (Retrieval-Augmented Generation) with source display
- Streaming responses for enhanced user experience
- Conversational memory for tracking interactions

In [817]:
#  Importation des bibliothèques
import os
import json
import getpass
import requests

from langchain_mistralai.chat_models import ChatMistralAI
from langgraph.graph import START, MessagesState, StateGraph
from langchain_core.messages import HumanMessage
from langgraph.checkpoint.memory import MemorySaver
from langchain_core.prompts import ChatPromptTemplate, PromptTemplate
from langchain_core.prompts import PipelinePromptTemplate

### Prompt definition

In [943]:
prompt_principal = ChatPromptTemplate.from_template(
    """
    Tu es **Crystal Bot**, un assistant intelligent d'orientation professionnelle.
    Tu dois fournir des réponses basées sur les informations récupérées.
    
    Ton objectif est d'aider chaque utilisateur à **clarifier son avenir** en lui proposant **des conseils sur-mesure et motivants**.

    **Contexte pertinent issu de la base de connaissances :** 
    {context}
    
    ➤ **Adapte-toi à l’utilisateur** : si indécis, propose des pistes d’exploration.
    ➤ **Si comparaison de plusieurs options**, aide-le à peser le pour et le contre.
    ➤ **Propose une réponse fluide, naturelle et pas trop longue**, qui ne se contente pas d’une liste figée, mais qui établit un dialogue et donne des solutions plus large.
    """
)

topic_prompt = PromptTemplate.from_template(
    """
    Analyse la question suivante et identifie le ou les domaines principaux auxquels elle appartient.

    Question: {input}

    Réponds en listant **un ou plusieurs domaines** parmi les suivants (séparés par une virgule) :
    - "Informatique et Numérique"
    - "Sciences et Ingénierie"
    - "Santé et Médecine"
    - "Droit et Sciences Politiques"
    - "Économie et Gestion"
    - "Sciences Sociales et Psychologie"
    - "Arts, Design et Culture"
    - "Lettres et Langues"
    - "Sciences de l'Éducation"
    - "Communication et Journalisme"
    - "Tourisme, Hôtellerie et Restauration"
    - "Environnement et Développement Durable"
    - "Sport et Activité Physique"
    - "Architecture et Urbanisme"
    - "Agronomie et Agroalimentaire"

    Si aucun domaine n’est clair, réponds uniquement par "Autre".

    Domaines identifiés :
    """
)


intent_prompt = PromptTemplate.from_template(
    """
    Analyse la question suivante et identifie l’intention principale de l’utilisateur :

    Question: {input}

    Réponds par l’une ou plusieurs des options suivantes :
    - "Métiers"
    - "Formations"
    - "Salaire"
    - "Offres d'emploi"
    - "Parcoursup"
    - "Autre"

    Intention détectée :
    """
)


chatbot_prompt = PromptTemplate.from_template(
    """
    
    Je suis **Crystal Bot**, ton conseiller d'orientation professionnelle. 🔮✨  
    
    L'utilisateur a demandé : {input}.
    Domaine détecté : {topic} (caché à l'utilisateur)
    Intention détectée : {intent} (caché à l'utilisateur)
    
  ➤ **Si l'intention est "Métiers"** :
        - Propose des **métiers adaptés** au profil de l’utilisateur en allant au-delà des évidences.   
        - Explique **les missions, conditions de travail et débouchés** en t’adaptant à la curiosité de l’utilisateur.  
        - **N’hésite pas à raconter une anecdote ou une tendance actuelle, personnalise la réponse** pour rendre la réponse plus vivante et personnalisée.  
        - **Fournis une vision inspirante et dynamique**, et pas seulement une simple liste de métiers.

    ➤ **Si l'intention est "Formations"** :
        - Présente des **formations pertinentes** mais **ajoute des alternatives originales** (double cursus, parcours atypiques).
        - Décris les options de manière dynamique : **BTS, Licence, Master, écoles spécialisées, mais aussi MOOC et certifications**.  
        - **Varie les approches selon la question de l’utilisateur**, sans donner toujours la même liste figée.
        - Rassure l’utilisateur en expliquant que *sa motivation est un facteur clé*. *Donne lui des conseils*
        - **N’hésite pas à raconter une anecdote ou une tendance actuelle, personnalise la réponse** pour rendre la réponse plus vivante et personnalisée. 
        - Si pertinent propose à l'utilisateur de visiter des salons pour en savoir plus sur les formations. 

    ➤ **Si l'intention est "Salaire"** :
        - Donne **un aperçu détaillé des salaires**, mais va au-delà des chiffres standards en ajoutant **les tendances du marché**.  
        - Explique **les différences selon l’expérience, le secteur, et la localisation**.  
        - **Si pertinent, parle des avantages indirects** (avantages en nature, perspectives d’évolution, travail à l’international).  
         - **N’hésite pas à raconter une anecdote ou une tendance actuelle, personnalise la réponse** pour rendre la réponse plus vivante et personnalisée.  

    ➤ **Si l'intention est "Offres d'emploi"** :
        - **Décris le marché actuel** du secteur concerné : quelles entreprises recrutent ? Quelles compétences sont recherchées ?
        - Donne **des conseils personnalisés** pour optimiser les candidatures, en fonction du domaine visé.
        - **Propose une approche proactive** : comment créer des opportunités, réseauter efficacement ou se démarquer ?  
         - **N’hésite pas à raconter une anecdote ou une tendance actuelle, personnalise la réponse** pour rendre la réponse plus vivante et personnalisée.  

    ➤ **Si l'intention est "Parcoursup"** :
        - **Explique Parcoursup en t’adaptant au profil de l’utilisateur** (lycéen stressé, étudiant en réorientation…).
        - Fournis **des conseils concrets pour réussir son dossier** et éviter les pièges.  
        - Fournis **des conseils concrets pour réussir la lettre de motivation** et se distinguer des autres candidats. 
        - Si pertinent, parle **des alternatives à Parcoursup** (écoles privées, études à l’étranger, admissions parallèles).  
    

    ➤ **Si l'intention est "Autre"** :
        - **Interprète la demande de l’utilisateur avec souplesse** et propose une réponse originale.  
        - Si possible, **ouvre la discussion sur des idées nouvelles** en fonction de son profil.
        - **Demande lui plus de précisions sur ce qu'il souhaite apprendre ou approfondir** en terme professionnel ou de formation.
         
    """
)


closing_prompt = PromptTemplate.from_template(
    """
    J’espère que cette réponse **t’a aidé à y voir plus clair !** 🔮  
    **As-tu d’autres questions ?** Je suis là pour explorer toutes les possibilités avec toi.  
    """
)

### Setting up conversation memory

In [823]:
# Mise en place de la mémoire conversationnelle
memory = MemorySaver()
workflow = StateGraph(state_schema=MessagesState)

def call_model(state: MessagesState):
    """Appelle le modèle avec historique de conversation"""
    response = llm.invoke(state["messages"])
    return {"messages": response}

workflow.add_edge(START, "model")
workflow.add_node("model", call_model)
chatbot = workflow.compile(checkpointer=memory)

## Creating the retrieval chain with LangChain

Creating a retrieval chain that, based on a user question, will retrieve relevant Documents from Chroma and provide them in context to the MistralAI language model to generate an informed answer

In [833]:
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain.chains import create_retrieval_chain
from langchain import hub

def build_retrieval_chain(vector_store, llm, k=5):
    """
    Build a retrieval chain using a given vector store and LLM
    
    Parameters:
        - vector_store: The vector store containing document embeddings
        - llm: The language model to generate responses
        - k: Number of most relevant document chunks to retrieve (default is 5)
    
    Returns:
        - retrieval_chain: A LangChain retrieval chain object.
    """
    # Create a retriever from the vector store
    retriever = vector_store.as_retriever(search_kwargs={"k": k})
    
    # Load a pre-defined prompt template for retrieval-based Q&A
    retrieval_chat_prompt = hub.pull("langchain-ai/retrieval-qa-chat")
    
    # Create a document combination chain
    combine_docs_chain = create_stuff_documents_chain(llm, retrieval_chat_prompt)
    
    # Create and return the retrieval chain
    return create_retrieval_chain(retriever, combine_docs_chain)

def retrieve_and_format_context(user_query, vector_store, llm):
    """Retrieve documents from vector store and format the context"""
    retrieval_chain = build_retrieval_chain(vector_store, llm)
    retrieved_docs = retrieval_chain.invoke({"input": user_query})

    documents = retrieved_docs["context"]

    formatted_context = "\n".join([doc.page_content for doc in documents])
    sources = [doc.metadata.get("source", "Unknown source") for doc in documents]

    return formatted_context, sources

## Building a full ChatBot response

In [845]:
def generate_response(user_query, vector_store, llm):
    """Generate an optimized response with CrystalBot and keep the history"""

    context, sources = retrieve_and_format_context(user_query, vector_store, llm)
    
    global conversation_history  # Utilisation d'une variable distincte pour stocker les messages

    # Charger l'historique des messages de manière locale
    past_messages = conversation_history if 'conversation_history' in globals() else []  

    # **🔹 Étape 1 : Détection du domaine / topic**
    topic_output = topic_prompt.format(input=user_query)

    # **🔹 Étape 2 : Détection de l’intention utilisateur**
    intent_output = intent_prompt.format(input=user_query)
    if not intent_output:
        intent_output = "Autre"

    # **🔹 Étape 3 : Génération de la réponse principale**
    chatbot_prompt_hidden = chatbot_prompt.format(
        input=user_query, 
        topic=topic_output, 
        intent=intent_output,
        context=context,
    )

    chatbot_output = chatbot_prompt_hidden.replace(topic_output, "").replace(intent_output, "")

    # **🔹 Étape 4 : Génération des suggestions d’exploration selon l’intention détectée**
    exploration_suggestions = ""

    if "Métiers" in intent_output:
        exploration_suggestions += """
        **🌍 Pour aller plus loin :**  
        - 🔍 **Découvre des métiers similaires** via des plateformes comme Onisep ou Studyrama.  
        - 🎭 **Participe à des salons professionnels** et rencontres avec des experts du domaine.  
        - 👥 **Échange avec des professionnels** sur LinkedIn ou lors d’événements.  
        """

    if "Formations" in intent_output or "Parcoursup" in intent_output:
        exploration_suggestions += """
        **📚 Pour approfondir ton parcours :**  
        - 🎤 **Découvre les parcours d’anciens étudiants** via des témoignages en ligne.  
        - 🔎 **Explore les formations en alternance** et internationales.  
        - 🏫 **Assiste aux journées portes ouvertes** des écoles et universités.  
        """

    if "Salaire" in intent_output:
        exploration_suggestions += """
        **💰 Pour mieux comprendre les salaires et évolutions de carrière :**  
        - 📊 **Consulte des études de rémunération** sur Glassdoor et l’APEC.  
        - 📈 **Analyse les évolutions de carrière possibles** en fonction de ton secteur.  
        """

    if "Offres d'emploi" in intent_output:
        exploration_suggestions += """
        **📝 Pour trouver des opportunités professionnelles :**  
        - 🔍 **Consulte des plateformes spécialisées** comme Indeed ou Pôle Emploi.  
        - 📩 **Optimise ton CV et ta lettre de motivation** pour te démarquer.  
        """

    if "Les deux" in intent_output:
        exploration_suggestions += """
        **🌟 Pour lier formations et métiers :**  
        - 📚 **Découvre les formations qui recrutent le plus**.  
        - 👀 **Explore les tendances de recrutement dans ton secteur**.  
        """

    if "Autre" in intent_output:
        exploration_suggestions += """
        **🔍 Explorons d’autres pistes !**  
        - 🤔 **Précise un peu plus ta demande**, veux-tu parler de reconversion, d’entrepreneuriat, d’études à l’étranger ?  
        - 💡 **Inspiration** : Parfois, explorer d’autres secteurs peut ouvrir des portes inattendues.  
        - 🔎 **Découvre des parcours inspirants** : interviews, conférences, podcasts sur des choix de carrière atypiques.  
        """

    # **🔹 Étape 5 : Conclusion dynamique**
    closing_output = closing_prompt.format()

    # ✅ **Ajout d’une introduction engageante pour la toute première réponse**
    intro_message = f"""
    Bonjour ! 😊  

    Je suis **Crystal Bot**, ton conseiller d'orientation professionnelle. 🔮✨  
    Mon objectif est de **t’aider à clarifier ton avenir** en te proposant des pistes adaptées et personnalisées.  
    Voici quelques idées et conseils pour t’aider à avancer :  
    """

    # ✅ **Création du message final à envoyer au modèle**
    final_prompt = f"""
    {intro_message}  

    **💡 Recommandation de Crystal Bot :**  
    {chatbot_output}  

    {exploration_suggestions}  

    {closing_output}  
    """

    # ✅ **Ajout du message dans l'historique**
    messages = past_messages + [HumanMessage(content=final_prompt)]

    # ✅ **Envoi de la requête complète au modèle**
    response = llm.invoke(messages)

    # ✅ **Mise à jour de l'historique de la conversation**
    conversation_history = messages + [response]

    return {
        "response": response.content,
        "sources": sources
    }

def refine_response(chatbot_output, user_query, llm):
    """Improve clarity and precision of response with LLM"""
    refinement_prompt = f"""
    Améliore la réponse suivante en la rendant plus précise et engageante :
    Contexte : {user_query}
    Réponse initiale : {chatbot_output}
    Réponse améliorée :
    """

    refined_response = llm.invoke([HumanMessage(content=refinement_prompt)]).content

    return refined_response

## Testing the ChatBot

In [863]:
user_query = "Quels métiers sont accessibles après un diplôme en informatique ?"

# Tester la récupération des documents depuis ChromaDB
context, sources = retrieve_and_format_context(user_query, vector_store, llm)

print("🔹 Contexte récupéré :")
print(context)
print("\n🔹 Sources associées :")
print(sources)

# Tester la réponse initiale générée par le chatbot
initial_result = generate_response(user_query, vector_store, llm)

print("\n🔹 Réponse initiale du chatbot :")
print(initial_result["response"])
print("\n🔹 Sources utilisées :")
print(initial_result["sources"])

# 🔥 Appel de refine_response pour améliorer la réponse
refined_result = refine_response(initial_result["response"], user_query, llm)

print("\n🔹 Réponse affinée du chatbot :")
print(refined_result)

🔹 Contexte récupéré :
en informatique est surtout accessible aux dipl\u00f4m\u00e9s de niveau bac\u00a0+\u00a04, +\u00a05\u00a0. Qu'il s'agisse des \u00e9coles d'ing\u00e9nieurs ou des universit\u00e9s, ces fili\u00e8res permettent d'acqu\u00e9rir une double comp\u00e9tence technologique et manag\u00e9riale. \u00c0 compl\u00e9ter par une exp\u00e9rience professionnelle de 5 ou 6\u00a0ans minimum.</p>\n            <p>Niveau bac\u00a0+\u00a05</p>\n            <p>Master en informatique</p>\n            <p>Dipl\u00f4me d'ing\u00e9nieur</p>\n            <p>Niveau bac\u00a0+\u00a06</p>\n            <p>Mast\u00e8re sp\u00e9cialis\u00e9</p>", "vie_professionnelle": "<h3>Salaire</h3>\n            <h5>Salaire du d\u00e9butant</h5>\n            <p>2915 euros brut par mois </p>\n            <h3>Int\u00e9grer le march\u00e9 du travail</h3>\n            <h5>Recrutements \u00e0 la hausse</h5>\n            <p>Secteur priv\u00e9 ou public : le poste de chef de projet b\u00e9n\u00e9ficie de recrutements

In [ ]:
user_query = "hello, quels métiers conseilles-tu à quelqu'un qui aime le contact avec les gens ?"

# Tester la récupération des documents depuis ChromaDB
context, sources = retrieve_and_format_context(user_query, vector_store, llm)

# Tester la réponse initiale générée par le chatbot
initial_result = generate_response(user_query, vector_store, llm)

# 🔥 Appel de refine_response pour améliorer la réponse
refined_result = refine_response(initial_result["response"], user_query, llm)

print(refined_result)

In [ ]:
user_query = "Je souhaite intégrer une CPGE scientifique. Peux-tu m'aider à rédiger ma lettre de motivation ?"

# Tester la récupération des documents depuis ChromaDB
context, sources = retrieve_and_format_context(user_query, vector_store, llm)

# Tester la réponse initiale générée par le chatbot
initial_result = generate_response(user_query, vector_store, llm)

# 🔥 Appel de refine_response pour améliorer la réponse
refined_result = refine_response(initial_result["response"], user_query, llm)

print(refined_result)

## Alternative (with COT + refinement)

In [857]:
def generate_response_with_cot(user_query, vector_store, llm):
    """ Génère une réponse en utilisant Chain of Thought et le LLM """

    context, sources = retrieve_and_format_context(user_query, vector_store, llm)
    
    # Étape 1 : Identification du sujet et de l'intention
    topic_output = llm.invoke([HumanMessage(content=topic_prompt.format(input=user_query))]).content
    intent_output = llm.invoke([HumanMessage(content=intent_prompt.format(input=user_query))]).content
    
    # Étape 2 : Génération d'une réponse avec le chatbot_prompt
    chatbot_input = chatbot_prompt.format(input=user_query, topic=topic_output, intent=intent_output)
    chatbot_output = llm.invoke([HumanMessage(content=chatbot_input)]).content

    # Étape 3 : Ajout d'un message de clôture
    closing_output = llm.invoke([HumanMessage(content=closing_prompt.format())]).content

    # ✅ Correction : Retourne un dictionnaire structuré
    return {
        "response": chatbot_output + "\n" + closing_output,
        "sources": sources
    }

In [ ]:
user_query = "Quels métiers sont accessibles après un diplôme en informatique ?"

# Tester la récupération des documents depuis ChromaDB
context, sources = retrieve_and_format_context(user_query, vector_store, llm)

# Tester la réponse initiale générée par le chatbot
initial_result = generate_response_with_cot(user_query, vector_store, llm)

# 🔥 Appel de refine_response pour améliorer la réponse
refined_result = refine_response(initial_result["response"], user_query, llm)

print("\n🔹 Réponse affinée du chatbot :")
print(refined_result)